###  An illustration of the McEliece system, one step at a time

In [71]:
import os 
os.chdir('C:\\Users\\usuario\\ownCloud\\public_html\\CC2')
# Current extension patch to CC
from CC_x import *

#### 0. Construct the binary field, and call it K

In [72]:
K = Zn(2,'K')

#### 1. Construct $F32$ with generator named 'a'

In [73]:
m = 5

[F,a] = extension(K,get_irreducible_polynomial(K,m),'a','F')

#### 2. Get a random monic irreductible polynomial $p$ in $F[T]$ of degree $t=3$

In [74]:
t = 3

g = get_irreducible_polynomial(F,t,'T')

show(g) 

T**3 + (a**4 + a + 1)*T**2 + (a**4 + a**3 + a)*T + a**4 + a**3 + a


#### 3. Create the Goppa code $C$ of $g$ over the non-zero elements of $F$ (expression $X[1:]$).  It corrects deg$(g) = 3 =t$ errors

In [75]:
X = Set(F)

n = len(X)-1

C = Goppa(g,X[1:])

#### 4. Control matrix of $C$ over $F$ and over $K$ 

In [84]:
HH = H_(C)

show(shape(HH),nl)

H1 = blow(HH,K)

show(shape(H1),nl)

k = rank(H1)

show(k,nl)

show(n-t*m)

(3, 31) 

(15, 31) 

15 

26


#### 5. Generating matrix over $K$, $G$. We see that $k = 16$

In [77]:
G = left_kernel(transpose(H1))

show(shape(G),nl)

(16, 31) 



#### 6. Matrix $S$ of the private key; $K$_$(G)$ is $K$,  as $C$ is defined over $K$. $S$ is an invertible binary matrix of order 16.

In [78]:
S=rd_GL(nrows(G),K_(G))

show(det(S),nl)

1 



#### 7 Matrix $P$ (with integer entries) of the private key.  det($P$) can be 1 or $-1$

In [79]:
P = rd_permutation_matrix(ncols(G))

show(det(P),nl)

-1 



#### 8 Public key (G1,t)

In [80]:
G1 = S*G*P

show(shape(G1),nl)

t = nrows(H_(C))//2

show(t)

(16, 31) 

1


#### 9 Encryption of a random information vector $u$

In [81]:
u = rd_vector(K,nrows(G1))

show(u,nl)

# coding with G1
x = u*G1 

show(x,nl)

# random vector of weight t = 3 of same length as x
e = rd_error_vector(K,len(x),t) 

show(e,nl)

# vector transmitted to receiver
x1 = x+e 
show(x1,nl)



[1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0] 

[1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1] 

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] 

[1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1] 



#### 10. Decrypting. The inverse of $P$ it its transpose

In [82]:
y = x1*transpose(P) 

show(y,nl)

# decrypting, with PGZ in this occasion
x2 = PGZ(y,C) 

show(x2,nl)

# get uG by linear algebra
u1 = solve_linear_system(transpose(G),transpose(x2))
u1 = transpose(u1)

show(u1,nl)

# undo the scrabbling by S
uu=u1/S

show(uu,nl)

# check that it coincides with the origial message
show(u,nl)

[0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 1] 

PGZ> Error positions and values [6] [1]
[0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 1] 

[1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1] 

[1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0] 

[1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0] 



In [83]:
show('uu = u ?')

show(uu == u,nl)

uu = u ?
True 

